<a href="https://colab.research.google.com/github/opivtorak/2017-21_cars_registration-dynamics_in_Ukraine/blob/main/network_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Intro

In [ ]:
langs = ["_uk", "_ru", "_nl", "_it", "_de", "_fr", "_en"]

In [ ]:
!pip install gravis

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 659 kB 7.0 MB/s 


In [ ]:
import os
import pandas as pd
import networkx as nx
import gravis as gv
import re
from collections import defaultdict

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


#Checks

In [ ]:
help(gv.d3)

Help on function d3 in module gravis._internal.plotting.d3:

d3(data, graph_height=450, details_height=100, show_details=False, show_details_toggle_button=True, show_menu=False, show_menu_toggle_button=True, show_node=True, node_size_factor=1.0, node_size_data_source='size', use_node_size_normalization=False, node_size_normalization_min=5.0, node_size_normalization_max=75.0, node_drag_fix=False, node_hover_neighborhood=False, node_hover_tooltip=True, show_node_image=True, node_image_size_factor=1.0, show_node_label=True, show_node_label_border=True, node_label_data_source='id', node_label_size_factor=1.0, node_label_rotation=0.0, node_label_font='Arial', show_edge=True, edge_size_factor=1.0, edge_size_data_source='size', use_edge_size_normalization=False, edge_size_normalization_min=0.2, edge_size_normalization_max=5.0, edge_curvature=0.0, edge_hover_tooltip=True, show_edge_label=False, show_edge_label_border=True, edge_label_data_source='id', edge_label_size_factor=1.0, edge_label_rot

In [ ]:
df = pd.read_csv("/content/drive/MyDrive/Project Bluff/data/Vizzes/keywords_dynamic_upd.csv")

In [ ]:
df.head(3)

word  year  platform       count
0  action  2018   twitter   10.209424
1  action  2021  telegram  196.529853
2  action  2022  telegram  195.024569

In [ ]:
tasks_folder = "/content/drive/MyDrive/Tasks/ru_accounts"
for filename in os.listdir(tasks_folder):
    f = os.path.join(tasks_folder, filename)
    if filename.endswith('csv'):
      df = pd.read_csv(f)
      retweets = df[df.isRetweet == True]
      print(len(retweets))

0
0
0


In [ ]:
tasks_folder = "/content/drive/MyDrive/Tasks"
all_df = pd.DataFrame()
for filename in os.listdir("/content/drive/MyDrive/Tasks"):
    f = os.path.join(tasks_folder, filename)
    if filename.endswith('_acc.csv') and '_de' in filename:
      print(filename)
      try:
        input_df = pd.read_csv(f)
        all_df = all_df.append(input_df, ignore_index=True)
      except pd.errors.EmptyDataError:
        pass
all_df = all_df.drop_duplicates()
print(len(all_df))

2014_twi_de_acc.csv
2015_twi_de_acc.csv
2018_twi_de_acc.csv
2019_twi_de_acc.csv
2021_twi_de_acc.csv
2022_twi_de_acc.csv
162115


In [ ]:
input_df = pd.read_csv("/content/drive/MyDrive/Tasks/2022_twi_de_acc.csv")
input_df = input_df.drop_duplicates()
input_df.to_csv("/content/drive/MyDrive/Tasks/2022_twi_de_acc_dedupl.csv", index=False)

#TG network

In [ ]:
tg_all_folder = "/content/drive/MyDrive/Project Bluff/data/TG-all"

In [ ]:
column_main = "Название источника"
column_from = "Репост из"

In [ ]:
def analyze_country(country_dir):
  all_df = pd.DataFrame()
  for filename in os.listdir(tg_all_folder+country_dir):
    f = os.path.join(tg_all_folder+country_dir, filename)
    if filename.endswith('csv'):
      try:
        input_df = pd.read_csv(f)
        all_df = all_df.append(input_df, ignore_index=True)
      except pd.errors.EmptyDataError:
        pass
  out_df = all_df[all_df["Репост из"] != None][["Название источника", "Репост из"]]
  out_df = out_df.groupby(["Название источника", "Репост из"]).size()
  out_df = out_df.to_frame(name = 'size').reset_index()
  out_df.rename(columns={"size": "weight"}, inplace=True)
  return out_df

In [ ]:
def assign_node_size_by_degree(graph):
    for node_id in graph.nodes:
      graph.nodes[node_id]["degree"] = 2 + graph.degree[node_id]
    return graph

##Belarus

In [ ]:
by_df = analyze_country("/Belarus-ru-2018-2022")
by_df2=by_df[by_df['weight']>5]
print(len(by_df2))

354


In [ ]:
G = nx.from_pandas_edgelist(by_df2, source=column_from, target=column_main, edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Russia

In [ ]:
ru_df = analyze_country("/Russia-ru-2018-2022")

In [ ]:
ru_df2 = ru_df[ru_df['weight']>20]
print(len(ru_df2))

682


In [ ]:
G = nx.from_pandas_edgelist(ru_df2, source=column_from, target=column_main, edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Ukraine (in ua and ru)

In [ ]:
ua_df_1 = analyze_country("/Ukraine-ru-2018-2022")
ua_df_2 = analyze_country("/Ukraine-UK-2018-2019--2021-2022")
ua_df = ua_df_1.append(ua_df_2, ignore_index=True)

In [ ]:
ua_df2 = ua_df[ua_df['weight']>10]
print(len(ua_df2))

309


In [ ]:
G = nx.from_pandas_edgelist(ua_df2, source=column_from, target=column_main, edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

#Twitter

In [ ]:
def create_df(lang):
  lang_df = pd.DataFrame()
  for filename in os.listdir("/content/drive/MyDrive/Twitter/Tasks/all_accs"):
    f = os.path.join("/content/drive/MyDrive/Twitter/Tasks/all_accs", filename)
    if filename.endswith('.csv') and lang in filename:
      print(filename)
      try:
        df = pd.read_csv(f)
      except pd.errors.EmptyDataError:
        pass
  lang_df = lang_df.append(df, ignore_index=True)
  lang_df['text'] = df['text'].str.replace('https?:[^ ]+', '', flags=re.IGNORECASE)
  out_df = lang_df[lang_df.duplicated('text', keep=False)].groupby('text')['name'].apply(list).reset_index()
  out_df['name2'] = out_df['name'].apply(set)
  out_df['N_of_accs'] = out_df['name2'].apply(lambda x: len(x))
  out_df = out_df[out_df['N_of_accs']>1]
  out_df['name2'] = out_df['name2'].apply(list)
  test_new = []
  for index, row in out_df.iterrows():
    for i in range(len(row['name2'])):
      for el in row['name2'][i+1:]:
        test_new.append((row['name2'][i], el))
  viz_df = pd.DataFrame(test_new, columns =['source', 'target'])
  viz_df = viz_df.groupby(viz_df.columns.tolist()).size().reset_index().\
    rename(columns={0:'weight'})
  return viz_df

##Ukrainian

In [ ]:
uk_viz_df = create_df("uk")

2014_twi_uk_acc.csv
2014_twi_uk2_acc.csv
2015_twi_uk_acc.csv
2015_twi_uk2_acc.csv
2018_twi_uk_acc.csv
2018_twi_uk2_acc.csv
2019_twi_uk2_acc.csv
2019_twi_uk_acc.csv
2021_twi_uk_acc.csv
2021_twi_uk2_acc.csv
2022_twi_uk_acc.csv
2022_twi_uk2_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
uk_viz_df

source               target  \
0                                         24 канал    Aleksey Kokorinov   
1                                         24 канал              LN NATO   
2                                         24 канал            Only News   
3                                         24 канал            Блок-інфо   
4                                         24 канал  ✙ Ukraine News UP ✙   
..                                             ...                  ...   
326                            ✙ Ukraine News UP ✙         News Ukraine   
327                            ✙ Ukraine News UP ✙            Ukrinform   
328                            ✙ Ukraine News UP ✙            Блок-інфо   
329                                ✙Осадчий пише ✙      Назар Приходько   
330   NFT 🔱💎 ⰉⰳⱁⱃѦⱀ ⚛︎ יִגוּריאןּ ✡︎  🥲 👽XÆA12 ꙮ        Радіо Свобода   

     weight  
0         1  
1         1  
2         2  
3         2  
4         2  
..      ...  
326       1  
327       1  
328      12  
329       1  
330       1  

[331 rows x 3 columns]

In [ ]:
G = nx.from_pandas_edgelist(uk_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##French

In [ ]:
fr_viz_df = create_df("fr")

2014_twi_fr_acc.csv
2015_twi_fr_acc.csv
2018_twi_fr_acc.csv
2019_twi_fr_acc.csv
2021_twi_fr_acc.csv
2022_twi_fr_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(fr_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##German

In [ ]:
de_viz_df = create_df("de")

2014_twi_de_acc.csv
2015_twi_de_acc.csv
2018_twi_de_acc.csv
2019_twi_de_acc.csv
2021_twi_de_acc.csv
2022_twi_de_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(de_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Italian


In [ ]:
it_viz_df = create_df("it")

2014_twi_it_acc.csv
2015_twi_it_acc.csv
2018_twi_it_acc.csv
2019_twi_it_acc.csv
2021_twi_it_acc.csv
2022_twi_it_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(it_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Dutch

In [ ]:
nl_viz_df = create_df("nl")

2014_twi_nl_acc.csv
2015_twi_nl_acc.csv
2018_twi_nl_acc.csv
2019_twi_nl_acc.csv
2021_twi_nl_acc.csv
2022_twi_nl_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(nl_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##English

In [ ]:
en_viz_df = create_df("en")

2014_twi_en_acc.csv
2015_twi_en_acc.csv
2018_twi_en_acc.csv
2019_twi_en_acc.csv
2021_twi_en_acc.csv
2022_twi_en_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(en_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Russian

In [ ]:
ru_viz_df = create_df("ru")

2014_twi_ru_acc.csv
2014_twi_ru2_acc.csv
2015_twi_ru2_acc.csv
2015_twi_ru_acc.csv
2018_twi_ru_acc.csv
2018_twi_ru2_acc.csv
2019_twi_ru2_acc.csv
2019_twi_ru_acc.csv
2021_twi_ru_acc.csv
2021_twi_ru2_acc.csv
2022_twi_ru_acc.csv
2022_twi_ru2_acc.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  if sys.path[0] == '':


In [ ]:
G = nx.from_pandas_edgelist(ru_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)

##Russian accounts (special, accounts from Ira's list)

In [ ]:
lang_df = pd.DataFrame()
for filename in os.listdir("/content/drive/MyDrive/Twitter/Tasks/ru_accounts"):
  f = os.path.join("/content/drive/MyDrive/Twitter/Tasks/ru_accounts", filename)
  if filename.endswith('.csv'):
    print(filename)
    try:
      df = pd.read_csv(f)
    except pd.errors.EmptyDataError:
      pass
lang_df = lang_df.append(df, ignore_index=True)
lang_df['text'] = df['text'].str.replace('https?:[^ ]+', '', flags=re.IGNORECASE)
out_df = lang_df[lang_df.duplicated('text', keep=False)].groupby('text')['name'].apply(list).reset_index()
out_df['name2'] = out_df['name'].apply(set)
out_df['N_of_accs'] = out_df['name2'].apply(lambda x: len(x))
out_df = out_df[out_df['N_of_accs']>1]
out_df['name2'] = out_df['name2'].apply(list)
test_new = []
for index, row in out_df.iterrows():
  for i in range(len(row['name2'])):
    for el in row['name2'][i+1:]:
      test_new.append((row['name2'][i], el))
viz_df = pd.DataFrame(test_new, columns =['source', 'target'])
ru_viz_df_2 = viz_df.groupby(viz_df.columns.tolist()).size().reset_index().\
  rename(columns={0:'weight'})

en_2014-2015.csv
en_2018-2019.csv
en_2021-2022.csv


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: FutureWarning: The default value of regex will change from True to False in a future version.
  # This is added back by InteractiveShellApp.init_path()


In [ ]:
G = nx.from_pandas_edgelist(ru_viz_df, source="source", target="target", edge_attr='weight')
G = assign_node_size_by_degree(G)
gv.d3(G, node_size_data_source='degree', use_node_size_normalization=True, node_size_normalization_max=40,
      edge_size_data_source='weight', use_edge_size_normalization=True, node_hover_neighborhood=True, edge_curvature=0.3)